In [2]:
import matplotlib
import matplotlib.pyplot as plt
import keras
import nltk
#nltk.download('punkt')
#nltk.download('stopwords')
#nltk.download('wordnet')
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from keras.utils.vis_utils import plot_model
from keras.models import Sequential, Model, load_model
from keras.layers import Conv2D, Dense, Flatten, Dropout, MaxPooling2D, BatchNormalization, Activation, Embedding, Input
from keras.layers.convolutional import Conv1D, MaxPooling1D
from keras.layers.merge import concatenate
from keras.preprocessing.image import ImageDataGenerator
from keras.callbacks import ReduceLROnPlateau
from keras.callbacks import ModelCheckpoint, EarlyStopping
import keras.optimizers as optimizers
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn import metrics
from sklearn import preprocessing
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import (train_test_split, GridSearchCV)
from sklearn.metrics import f1_score,accuracy_score,confusion_matrix,precision_score,recall_score,auc, roc_curve, roc_auc_score
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import (LabelEncoder,OneHotEncoder, StandardScaler)  
from sklearn import model_selection
import joblib
from pickle import dump
from sklearn.preprocessing import QuantileTransformer
import seaborn as sns; sns.set(style="ticks", color_codes=True)
import json
import math
import os
import shutil
import zipfile
import pickle
import statistics
import tensorflow as tf
import pandas as pd
import numpy as np
from datetime import datetime
import glob
from pandas import Series
import csv
import sys
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.chrome.options import Options
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.common.by import By
from selenium.webdriver.support import expected_conditions as EC
from selenium.common.exceptions import TimeoutException
from selenium.common.exceptions import NoSuchElementException
from selenium.common.exceptions import StaleElementReferenceException
from random import randint
import time
import re

In [2]:
X_train_metadata = np.load('Demo_objects/metadata_X_train.npy',allow_pickle=True)
X_test_metadata = np.load('Demo_objects/metadata_X_test.npy',allow_pickle=True)
X_train_description = np.load('Demo_objects/description_X_train.npy',allow_pickle=True)
X_test_description = np.load('Demo_objects/description_X_test.npy',allow_pickle=True)
X_train_comments = np.load('Demo_objects/comments_X_train.npy',allow_pickle=True)
X_test_comments = np.load('Demo_objects/comments_X_test.npy',allow_pickle=True)
y_train = np.load('Demo_objects/description_Y_train.npy',allow_pickle=True)
y_test = np.load('Demo_objects/description_Y_test.npy',allow_pickle=True)

In [3]:
X_test_metadata

array([[4.99900005e-05, 1.13259302e-06, 1.44444444e-01, 1.39534884e-01,
        1.59948585e-05, 6.43382353e-05],
       [5.99900006e-05, 9.23918654e-06, 2.66666667e-01, 9.30232558e-02,
        1.56574669e-04, 2.78492647e-04],
       [3.49900003e-05, 2.52810942e-08, 3.22222222e-01, 1.16279070e-01,
        2.49919664e-07, 3.67647059e-05],
       ...,
       [3.34900003e-05, 7.92392504e-07, 3.22222222e-01, 4.65116279e-02,
        7.49758991e-06, 5.51470588e-05],
       [2.99990003e-04, 9.24656019e-07, 3.22222222e-01, 6.97674419e-02,
        7.83498146e-05, 4.59558824e-05],
       [4.99900005e-05, 4.61266204e-05, 3.22222222e-01, 9.30232558e-02,
        6.51415603e-04, 7.62867647e-05]])

In [4]:
print("Por favor, ingrese el URL del proyecto que desea analizar:\n")
url_input = input()
url_input = url_input + '?'

Por favor, ingrese el URL del proyecto que desea analizar:

https://www.kickstarter.com/projects/myticktalk/ticktalk-4?ref=discovery_category_ending_soon


In [4]:
print("Por favor, ingrese el URL del proyecto que desea analizar:\n")
url_input = input()
url_input = url_input + '?'

Por favor, ingrese el URL del proyecto que desea analizar:

https://www.kickstarter.com/projects/2125914059/revopoint-pop-high-precision-3d-scanner-for-3d-printing?ref=discovery_category_ending_soon


# Scraping metadata

In [5]:
url_input_metadata = url_input[:url_input.find('?')] + '/'
url_input_metadata

'https://www.kickstarter.com/projects/myticktalk/ticktalk-4/'

In [6]:
useless_characters = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642"
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)

options = Options()
#options.headless = True
#options.add_argument("--window-size=1920,1200")

DRIVER_PATH = 'C:/Drivers/webdrivers/chromedriver.exe'

def getPageMetadata(url):
    driver = webdriver.Chrome(options=options)
    driver.set_page_load_timeout(60)
    driver.get(url)
    
    # ===== PARTE DE "PLEDGE_AMOUNT" =====
    # Buscar elementos de la clase "pledge_amount"
    find_pledges = driver.find_elements_by_css_selector('h2.pledge__amount')
    pledge_amounts = []
    for pledge in find_pledges:
        # Para eliminar elementos que no sean los dígitos del monto de contribución
        pledge_number = re.sub("[^\d]", "", pledge.text)
        pledge_amounts.append(pledge_number)
            
    pledge_amounts = ' '.join(pledge_amounts).split()      # Para quitar campo vacío de la contribución libre
        
    pledge_amounts_list = []
    for pledge in pledge_amounts:
        pledge_number = int(pledge)
        pledge_amounts_list.append(pledge_number)

    pledge_amounts_list = list(dict.fromkeys(pledge_amounts_list))
    pledge_amounts_list.sort()
        
    # ===== PARTE DE "GOAL", PLEDGED", "DURATION" =====
    find_elements = driver.find_elements_by_class_name('bg-grey-100')
    find_elements = json.loads(find_elements[-1].get_attribute('data-initial'))  #El último elemento tiene toda la metadata
    goal = int(float(find_elements['project']['goal']['amount']))
    pledged = int(float(find_elements['project']['pledged']['amount']))
    completness = int(find_elements['project']['percentFunded'])
    duration = int(find_elements['project']['duration'])
    currency = find_elements['project']['currency']
    
    del pledge_amounts
    print(find_elements['project']['name'])
    driver.quit()
    time.sleep(randint(1,10))
    return [pledge_amounts_list,goal,pledged,completness,duration,currency]

In [7]:
metadata_output = getPageMetadata(url_input_metadata)
# Primer elemento: lista de montos para contribuir
# Segundo elemento: meta de campaña
# Tercer elemento: monto contribuido total
# Cuarto elemento: porcentaje contribuido (completitud)
# Quinto elemento: duración
metadata_output
metadata_pledges_num = len(metadata_output[0])
metadata_pledges_median = statistics.median(metadata_output[0])
metadata_goal = metadata_output[1]
metadata_pledged = metadata_output[2]
#metadata_completness = (metadata_pledged/metadata_goal)*100.0
metadata_completness = metadata_output[3]
metadata_duration = metadata_output[4]
metadata_currency = metadata_output[5]
print("Cantidad de montos de contribución disponibles:",metadata_pledges_num)
print("Mediana de montos de contribución disponibles:",metadata_pledges_median)
print("Meta de la campaña:",metadata_goal,metadata_currency)
print("Monto contribuído en la campaña:",metadata_pledged,metadata_currency)
print("Porcentaje contribuído:",metadata_completness,'%')
print("Duración de la campaña:",metadata_duration)

TickTalk 4: The Advanced 4G/LTE Smartwatch for Kids
Cantidad de montos de contribución disponibles: 8
Mediana de montos de contribución disponibles: 247.5
Meta de la campaña: 20000 USD
Monto contribuído en la campaña: 171580 USD
Porcentaje contribuído: 857 %
Duración de la campaña: 15


# Scraping descripciones

In [8]:
url_input_description = url_input[:url_input.find('?')] + '/description'
url_input_description

'https://www.kickstarter.com/projects/myticktalk/ticktalk-4/description'

In [9]:
useless_characters = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)
Newlines = re.compile(r'[\r\n]\s+')

options = Options()
#options.headless = True
#options.add_argument("--window-size=1920,1200")

DRIVER_PATH = 'C:/Drivers/webdrivers/chromedriver.exe'

def getPageDescription(url):
    driver = webdriver.Chrome(options=options, executable_path=DRIVER_PATH)
    driver.set_page_load_timeout(30)
    driver.get(url)
    time.sleep(15)  #Espera 15 mientras resolvemos captcha
    
    try:
        description_box = driver.find_element_by_css_selector('div.rte__content')
        # Encontrar todos los párrafos
        description_box = description_box.find_elements_by_tag_name("p")
        # Crear array vacío donde se almacenará el contenido descargado
        project_description = []
        # Iteración para agregando en lista cada descripción descargada
        for paragraph in description_box:
            project_description.append(paragraph.text)
        # Juntar párrafos separados en un solo vector, separándolos con un espacio
        project_description = ' '.join(project_description)
        # Eliminar caracteres especiales
        project_description = project_description.replace(u'\xa0', u'')
        project_description = project_description.replace(u'\n', u' ')
    # Y el except sirve para llenar valores nulos en el array en caso de error
    except (IndexError, ValueError):
        project_description = 'null'
    driver.quit()
    # Eliminar saltos de línea
    return Newlines.sub('\n', project_description)

In [10]:
description_output = getPageDescription(url_input_description)
description_output

"TickTalk 4 is the revolutionary 4G/LTE smartwatch phone designed for children ages 5-12 combining video and voice calling, secure messaging, parental controls, locating capability, SOS contacts, reminders, and more in one simple device.  The TickTalk 4 has all the essential features backers loved in the TickTalk 3 and introduces free streaming music powered by iHeartRadio Family, step tracking, 2x 5MP Selfie and Snapshot photo and video cameras, and new parental controls for the smartest smartwatch for kids.  No family should have to choose between peace of mind or technology when it comes to their children. TickTalk 4 gives children all the positive aspects of technology with a focus on safety, connection, and building better habits. TickTalk gives the modern family a safe cell phone alternative that over 190,000 families around the world have trusted since launching our first generation in 2016.  TickTalk 4 comes with 2-way voice, video, and Wi-Fi calling for crystal-clear connectin

# Scraping comentarios

In [11]:
url_input_comments = url_input[:url_input.find('?')] + '/comments'
url_input_comments

'https://www.kickstarter.com/projects/myticktalk/ticktalk-4/comments'

In [12]:
useless_characters = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags (iOS)
        u"\U00002500-\U00002BEF"  # chinese char
        u"\U00002702-\U000027B0"
        u"\U00002702-\U000027B0"
        u"\U000024C2-\U0001F251"
        u"\U0001f926-\U0001f937"
        u"\U00010000-\U0010ffff"
        u"\u2640-\u2642" 
        u"\u2600-\u2B55"
        u"\u200d"
        u"\u23cf"
        u"\u23e9"
        u"\u231a"
        u"\ufe0f"  # dingbats
        u"\u3030"
                      "]+", re.UNICODE)

options = Options()
#options.headless = True
#options.add_argument("--window-size=1920,1200")

DRIVER_PATH = 'C:/Drivers/webdrivers/chromedriver.exe'

def getPageComments(url):
    driver = webdriver.Chrome(options=options, executable_path=DRIVER_PATH)
    driver.get(url)
    
    time.sleep(30)  #Espera 30 mientras resolvemos captcha
    #Acá se presiona el botón de "Cargar más comentarios" hasta que ya no salga más
    while True:
        try:
            loadMoreButton = driver.find_element_by_css_selector('#react-project-comments > div > button')
            time.sleep(2)
            loadMoreButton.click()
            time.sleep(5)
        except (NoSuchElementException, StaleElementReferenceException):
            break

    time.sleep(5)  #Espera 5 segundos antes de continuar
    #comments = driver.find_elements_by_css_selector('div.w100p')
    
    try:
        #Para extraer todos los comentarios, incluyendo la marca "Creador" al costado de su comentario respectivo
        comments = driver.find_elements_by_css_selector('span.bg-ksr-green-700.white.px1.type-14.mr1, div.w100p')
        project_paragraphs = []
        for paragraph in comments:
            project_paragraphs.append(paragraph.text)

        # Obteniendo los índices de los comentarios del creador    
        idx_comment_creador = [i for i in range(len(project_paragraphs)) if project_paragraphs[i] == "Creador"] 
        idx_comment_creador = [i+1 for i in idx_comment_creador]

        # Eliminando los comentarios del creador
        for index in sorted(idx_comment_creador, reverse=True):
            del project_paragraphs[index]

        # Otra vez obteniendo el índice pero donde dice "Creador"    
        idx_comment_creador = [i for i in range(len(project_paragraphs)) if project_paragraphs[i] == "Creador"]

        # Eliminando donde dice "creador"
        for index in sorted(idx_comment_creador, reverse=True):
            del project_paragraphs[index]

        # Eliminando comentarios que fueron removidos
        project_paragraphs = [x for x in project_paragraphs if ("Este comentario") not in x]
        project_paragraphs = [x for x in project_paragraphs if ("0:00") not in x]
        project_paragraphs = [x for x in project_paragraphs if ("Mostrando") not in x]
        project_paragraphs = [x for x in project_paragraphs if ("Recordarme") not in x]
        project_paragraphs = [x for x in project_paragraphs if x]

        # Crear array vacío donde se almacenará el contenido descargado final
        project_comments = []
        for project_text in project_paragraphs:
            project_text = project_text.replace(u'\xa0', u'')
            project_text = project_text.replace(u'\n', u' ')
            project_text = re.sub(useless_characters, '', project_text)   #Para eliminar emojis y otros símbolos
            project_comments.append(project_text)

        del(project_paragraphs)  #Borrando para no ocupar mucha memoria
        #project_comments = ' '.join(project_comments)    #Para concatenar todos los comentarios en 1 array
    # Y el except sirve para llenar valores nulos en el array en caso de error
    except (IndexError, ValueError):
        project_comments = 'kuwagatabaizan'
    driver.quit()
    return project_comments

In [13]:
comments_output = getPageComments(url_input_comments)
comments_output

['Will Spotify work?',
 'Thank you! Could you integrate the Pix Mini app? https://www.kickstarter.com/projects/pixbackpack/pix-mini-the-first-smart-backpack-for-kids',
 'Do the headphones have an auxiliary input if wanting to connect it to an iPad?',
 'Will it work in Brazil?',
 'I’ve been using TickTalk3 for 2 years. Is it still eligible for trade in with Kickstarter?',
 'Will you offer backer TickTalk 4 in White Color?',
 'Will you allow backer to buy Ticktalk 3 as an add-on item, with special discount? My daughter still loves her Tick Talk 3 design, unfortunately, its screen was broken for just 2 months.',
 'when do I choose a color?',
 'Hi, i have tmobile and they said this would work if we opened a smartwatch line instead of a separate phone line. They said i can use the app to monitor and call/text her. Is this true?',
 'This is e x a c t l y what I have been looking for for my 7 year old for years! I am so excited for release. Thank you for making this!',
 'So if we purchased th

# Transformando inputs

## Metadata

In [14]:
#!pip install -v scikit-learn==0.22.2.post1 --user
# Cargando el escalador MinMax para la metadata
metadata_scaler = pickle.load(open('Demo_objects/metadata_scaler.pkl', 'rb'))

def MetadataInputProcessing(variable1,variable2,variable3,variable4,variable5,variable6):
    input_model = [variable1,variable2,variable3,variable4,variable5,variable6]
    input_model = np.array(input_model)
    input_model = np.reshape(input_model, (-1, 1))   # Para darle forma de 1 columna x 6 filas (y luego funcione el scaler)
    input_transformed = metadata_scaler.fit_transform(input_model)
    input_transformed = np.reshape(input_transformed, (1, -1))
    print('Dimensión de nueva input Metadata transformada:',input_transformed.shape)
    print('Input transformada:\n',input_transformed)
    return input_transformed

In [15]:
metadata_input_processed = MetadataInputProcessing(metadata_goal,metadata_completness,metadata_duration,metadata_pledges_num,metadata_pledged,metadata_pledges_median)

Dimensión de nueva input Metadata transformada: (1, 6)
Input transformada:
 [[1.16522510e-01 4.94835987e-03 4.07991980e-05 0.00000000e+00
  1.00000000e+00 1.39591542e-03]]


In [16]:
metadata_input_processed

array([[1.16522510e-01, 4.94835987e-03, 4.07991980e-05, 0.00000000e+00,
        1.00000000e+00, 1.39591542e-03]])

## Descripción

In [17]:
def DescriptionInputProcessing(text):
    new_text = re.sub(r'https?://\S+|Https?://\S+|www\.\S+|www\S+|\w+\.com','',text)
    new_text = re.sub(':‑\)|:\)|:-]|:]|:D|:p|:P|B^D|xD|8D|x‑D|8‑D|XD|=D|;\)|;‑\)|D:|D=|:o|:‑O|:O|:\(', '', new_text) #remover emoticons
    new_text = re.sub('[!*)@#%(&$_?^></-]', ' ', new_text) #remover caracteres especiales
    new_text = re.sub(r'[0-9]+', '', new_text) #remover números incluido decimales
    new_text = re.sub('(\\b[A-Za-z] \\b|\\b [A-Za-z]\\b)', '', new_text) #remove single characters
    new_text = new_text.lower()
    #new_text = word_tokenize(new_text)
    #tokenizer = nltk.tokenize.WhitespaceTokenizer()
    tokenizer = nltk.tokenize.TreebankWordTokenizer()
    new_text = tokenizer.tokenize(new_text)
    re_stopwords = []
    stop_words = set(stopwords.words('english'))
    for word in new_text:
        if word not in stop_words:
            re_stopwords.append(word)
    new_text = re_stopwords
    del re_stopwords
    lemmatizer = WordNetLemmatizer()
    lemmas = []
    for word in new_text:
        word1 = lemmatizer.lemmatize(word, pos = "n")      #Lematizando con NLTK
        word2 = lemmatizer.lemmatize(word1, pos = "v")
        word3 = lemmatizer.lemmatize(word2, pos = ("a"))
        lemmas.append(word3)
    new_text = lemmas
    del lemmas
    new_text = " ".join(new_text).strip()
    new_text = re.sub(r'[^\w\s]',' ',new_text) #remover caracteres de puntuación
    new_text = re.sub('(\\b[A-Za-z] \\b|\\b [A-Za-z]\\b)', '', new_text) #remove single characters
    new_text = re.sub(r'\s+', ' ', new_text) #remover múltiples espacios
    new_text = new_text.strip() #remover múltiples espacios
    print(new_text)
    return new_text

In [18]:
description_input_processed = DescriptionInputProcessing(description_output)

ticktalk revolutionary lte smartwatch phone design child age combine video voice call secure message parental control locate capability so contact reminder one simple device ticktalk essential feature backer love ticktalk introduce free stream music power iheartradio family step track mp selfie snapshot photo video camera new parental control smart smartwatch kids family choose peace mind technology come children ticktalk give child positive aspect technology focus safety connection build good habits ticktalk give modern family safe cell phone alternative family around world trust since launch first generation ticktalk come way voice video wi fi call crystal clear connecting add parent approve contact designate so shortcut parent icons secure firewall system block unknown number protect child contact unknown numbers end end encrypt message center choose individual group chat keep child connect people matter most unlimited customize preset text response preloaded response voice message 

In [19]:
# Cargando el tokenizer entrenado para la descripción
description_tokenizer = pickle.load(open('Demo_objects/tokenizer_description.pickle', 'rb'))

description_vocab_size = len(description_tokenizer.word_index) + 1
print('Tamaño del vocabulario entrenado de descripción: %d' % description_vocab_size)

# Codificando nuestro texto limpio de descripción con el tokenizer entrenado
def encoding_text(tokenizer, text, length):
    text = tokenizer.texts_to_sequences([text])    #La función texts_to_sequences funciona con lista de varios textos
    # Fuente: https://stackoverflow.com/questions/51956000/what-does-keras-tokenizer-method-exactly-do
    flat_list = []
    for sublist in text:
        for item in sublist:
            flat_list.append(item)
            
    flat_list = [flat_list]
    encoded_text = pad_sequences(flat_list, padding='post', maxlen=length)
    print('Longitud del texto procesado:',len(text))
    print('Dimensión de texto codificado:',encoded_text.shape)
    print('Texto codificado:\n',encoded_text)
    return encoded_text

Tamaño del vocabulario entrenado de descripción: 148270


In [20]:
print('Diccionario entrenado:\n',description_tokenizer.word_index)

Diccionario entrenado:
 {'<OOV>': 1, 'use': 2, 'make': 3, 'design': 4, 'need': 5, 'time': 6, 'work': 7, 'get': 8, 'app': 9, 'one': 10, 'help': 11, 'also': 12, 'project': 13, 'want': 14, 'u': 15, 'create': 16, 'like': 17, 'product': 18, 'user': 19, 'build': 20, 'people': 21, 'new': 22, 'go': 23, 'device': 24, 'de': 25, 'take': 26, 'allow': 27, 'system': 28, 'way': 29, 'first': 30, 'year': 31, 'support': 32, 'would': 33, 'see': 34, 'world': 35, 'start': 36, 'provide': 37, 'video': 38, 'power': 39, 'include': 40, 'many': 41, 'come': 42, 'even': 43, 'technology': 44, 'know': 45, 'find': 46, 'feature': 47, 'good': 48, 'give': 49, 'easy': 50, 'fund': 51, 'experience': 52, 'high': 53, 'kickstarter': 54, 'able': 55, 'well': 56, 'light': 57, 'goal': 58, 'develop': 59, 'control': 60, 'software': 61, 'set': 62, 'add': 63, 'part': 64, 'look': 65, 'test': 66, 'phone': 67, 'development': 68, 'team': 69, 'base': 70, 'life': 71, 'share': 72, 'application': 73, 'market': 74, 'available': 75, 'cost': 76

In [21]:
description_input_encoded = encoding_text(description_tokenizer, description_input_processed, 3671)

Longitud del texto procesado: 1
Dimensión de texto codificado: (1, 3671)
Texto codificado:
 [[   1 1508 5210 ...    0    0    0]]


In [22]:
description_input_encoded

array([[   1, 1508, 5210, ...,    0,    0,    0]])

In [23]:
reverse_word_index_description = dict([(value, key) for (key, value) in description_tokenizer.word_index.items()])

def decoding_description(text):
    return ' '.join([reverse_word_index_description.get(i, '?') for i in text[0]])

print('Decodificando descripción con data entrenada:\n',decoding_description(description_input_encoded))

Decodificando descripción con data entrenada:
 <OOV> revolutionary lte smartwatch phone design child age combine video voice call secure message parental control locate capability so contact reminder one simple device <OOV> essential feature backer love <OOV> introduce free stream music power iheartradio family step track mp selfie snapshot photo video camera new parental control smart smartwatch <OOV> family choose peace mind technology come <OOV> <OOV> give child positive aspect technology focus safety connection build good <OOV> <OOV> give modern family safe cell phone alternative family around world trust since launch first generation <OOV> come way voice video wi fi call crystal clear <OOV> add parent approve contact designate so shortcut parent <OOV> secure firewall system block unknown number protect child contact unknown <OOV> end end encrypt message center choose individual group chat keep child connect people matter <OOV> unlimited customize preset text response preloaded res

## Comentarios

In [24]:
def CommentsInputProcessing(text):
    new_text = ' '.join(text)
    new_text = re.sub(r'https?://\S+|Https?://\S+|www\.\S+|www\S+|\w+\.com','',new_text)
    new_text = re.sub(':‑\)|:\)|:-]|:]|:D|:p|:P|B^D|xD|8D|x‑D|8‑D|XD|=D|;\)|;‑\)|D:|D=|:o|:‑O|:O|:\(', '', new_text) #remover emoticons
    new_text = re.sub('[!*)@#%(&$_?^></-]', ' ', new_text) #remover caracteres especiales
    new_text = re.sub(r'[0-9]+', '', new_text) #remover números incluido decimales
    new_text = re.sub('(\\b[A-Za-z] \\b|\\b [A-Za-z]\\b)', '', new_text) #remove single characters
    new_text = new_text.lower()
    #new_text = word_tokenize(new_text)
    #tokenizer = nltk.tokenize.WhitespaceTokenizer()
    tokenizer = nltk.tokenize.TreebankWordTokenizer()
    new_text = tokenizer.tokenize(new_text)
    re_stopwords = []
    stop_words = set(stopwords.words('english'))
    for word in new_text:
        if word not in stop_words:
            re_stopwords.append(word)
    new_text = re_stopwords
    del re_stopwords
    lemmatizer = WordNetLemmatizer()
    lemmas = []
    for word in new_text:
        word1 = lemmatizer.lemmatize(word, pos = "n")      #Lematizando con NLTK
        word2 = lemmatizer.lemmatize(word1, pos = "v")
        word3 = lemmatizer.lemmatize(word2, pos = ("a"))
        lemmas.append(word3)
    new_text = lemmas
    del lemmas
    new_text = " ".join(new_text).strip()
    new_text = re.sub(r'[^\w\s]',' ',new_text) #remover caracteres de puntuación
    new_text = re.sub('(\\b[A-Za-z] \\b|\\b [A-Za-z]\\b)', '', new_text) #remove single characters
    new_text = re.sub(r'\s+', ' ', new_text) #remover múltiples espacios
    new_text = new_text.strip() #remover múltiples espacios
    print(new_text)
    return new_text

In [25]:
comments_input_processed = CommentsInputProcessing(comments_output)

spotify work thank could integrate pix mini app headphone auxiliary input want connect ipad work brazil use ticktalk years still eligible trade kickstarter offer backer ticktalk white color allow backer buy ticktalk add item special discount daughter still love tick talk design unfortunately screen break months choose color hi tmobile say would work open smartwatch line instead separate phone line say use app monitor call text her true look year old year excite release thank make purchase tt reimburse tt mail back refund amount card hd call ticktalk maximum duration per call would additional charge cable available separate purchase wait release able order granddaughter refuse go anywhere without tt favorite color blue go thrill that all new color options happen birthday may th go shock birthday gift year thank great product keep good work know feel safe watch wait since oct hope get soon excite watch glad bluetooth integrate also excite bluetooth integrate lte band ticktalk support fri

In [26]:
# Cargando el tokenizer entrenado para la descripción
comments_tokenizer = pickle.load(open('Demo_objects/tokenizer_comments.pickle', 'rb'))

comments_vocab_size = len(comments_tokenizer.word_index) + 1
print('Tamaño del vocabulario entrenado de descripción: %d' % comments_vocab_size)

Tamaño del vocabulario entrenado de descripción: 74096


In [27]:
print('Diccionario entrenado:\n',comments_tokenizer.word_index)

Diccionario entrenado:
 {'<OOV>': 1, 'get': 2, 'receive': 3, 'thank': 4, 'would': 5, 'update': 6, 'use': 7, 'work': 8, 'one': 9, 'ship': 10, 'like': 11, 'project': 12, 'backer': 13, 'go': 14, 'still': 15, 'please': 16, 'product': 17, 'time': 18, 'make': 19, 'good': 20, 'look': 21, 'back': 22, 'money': 23, 'see': 24, 'know': 25, 'also': 26, 'hi': 27, 'kickstarter': 28, 'think': 29, 'wait': 30, 'refund': 31, 'u': 32, 'send': 33, 'say': 34, 'want': 35, 'need': 36, 'great': 37, 'really': 38, 'pledge': 39, 'could': 40, 'try': 41, 'well': 42, 'email': 43, 'creator': 44, 'return': 45, 'mine': 46, 'even': 47, 'track': 48, 'app': 49, 'guy': 50, 'take': 51, 'way': 52, 'kuwagatabaizan': 53, 'yet': 54, 'order': 55, 'come': 56, 'day': 57, 'give': 58, 'new': 59, 'number': 60, 'thing': 61, 'campaign': 62, 'support': 63, 'seem': 64, 'much': 65, 'charge': 66, 'today': 67, 'week': 68, 'since': 69, 'people': 70, 'last': 71, 'find': 72, 'issue': 73, 'right': 74, 'first': 75, 'long': 76, 'hope': 77, 'rewar

In [28]:
comments_input_encoded = encoding_text(comments_tokenizer, comments_input_processed, 5000)
# Como la cantidad de comentarios es muy grande, se codifican solo las últimas 5000 palabras

Longitud del texto procesado: 1
Dimensión de texto codificado: (1, 5000)
Texto codificado:
 [[2360    8    4 ...    0    0    0]]


In [29]:
reverse_word_index_comments = dict([(value, key) for (key, value) in comments_tokenizer.word_index.items()])

def decoding_comments(text):
    return ' '.join([reverse_word_index_comments.get(i, '?') for i in text[0]])

print('Decodificando comentarios con data entrenada:\n',decoding_comments(comments_input_encoded))

Decodificando comentarios con data entrenada:
 spotify work thank could integrate pix mini app headphone auxiliary input want connect ipad work brazil use <OOV> <OOV> still eligible trade kickstarter offer backer <OOV> white color allow backer buy <OOV> add item special discount daughter still love tick talk design unfortunately screen break <OOV> choose color hi tmobile say would work open smartwatch line instead separate phone line say use app monitor call text <OOV> true look year old year excite release thank make purchase tt reimburse tt mail back refund amount card hd call <OOV> maximum duration per call would additional charge cable available separate purchase wait release able order granddaughter refuse go anywhere without tt favorite color blue go thrill <OOV> <OOV> new color <OOV> happen birthday may th go shock birthday gift year thank great product keep good work know feel safe watch wait since oct hope get soon excite watch glad bluetooth integrate also excite bluetooth in

# Prediciendo con modelo final

In [30]:
# Cargando modelo guardado
stacked_model_path = 'best_stacked_model.h5'
loaded_stacked_model = load_model(stacked_model_path)
loaded_stacked_model.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
Embedding_description_input (In [(None, 3671)]       0                                            
__________________________________________________________________________________________________
ensemble_1_Embedding_descriptio (None, 3671, 100)    14827000    Embedding_description_input[0][0]
__________________________________________________________________________________________________
dense_input (InputLayer)        [(None, 6)]          0                                            
__________________________________________________________________________________________________
ensemble_1_conv1d (Conv1D)      (None, 3667, 128)    64128       ensemble_1_Embedding_description[
______________________________________________________________________________________________

In [31]:
stacked_model_input = [description_input_encoded, comments_input_encoded, metadata_input_processed]
prediction = loaded_stacked_model.predict(stacked_model_input)
print('Predicción de probabilidad de financiamiento:',round(prediction[0][0]*100,2),'%')
print('Estado final de la campaña será: EXITOSO') if prediction[0][0] >= 0.5 else print('Estado final de la campaña será: FRACASADO')

Predicción de probabilidad de financiamiento: 99.65 %
Estado final de la campaña será: EXITOSO
